# Chapter 16 - Inference for Regression

In [ ]:
from datascience import *
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plots

In [ ]:
education = Table().read_table("grades_and_piazza.csv")
education

## 16.2 - Inference for the True Slope

In [ ]:
education.scatter(column_for_x="views", select="GPA", fit_line=True)

In [ ]:
def standard_units(numbers):
    "Convert any array of numbers to standard units."
    return (numbers - np.mean(numbers))/np.std(numbers)

def correlation(t, label_x, label_y):
    "Calculate r"
    return np.mean(standard_units(t.column(label_x))*standard_units(t.column(label_y)))

def slope(t, label_x, label_y):
    "Calculate m of y = mx + b"
    r = correlation(t, label_x, label_y)
    return r*np.std(t.column(label_y))/np.std(t.column(label_x))

In [ ]:
correlation(education, "views", "GPA")

One way to estimate the true slope is to use the slope of the regression line:

In [ ]:
slope(education, "views", "GPA")

We can also estimate the true slope by bootstrapping the original sample!

In [ ]:
def one_bootstrap_slope(table, x_column, y_column):
    bootstrap_sample = table.sample()
    return slope(bootstrap_sample, x_column, y_column)

def many_bootstrap_slopes(how_many, table, x_column, y_column):
    slopes = make_array()
    for _ in np.arange(how_many):
        slopes = np.append(slopes, one_bootstrap_slope(table, x_column, y_column))
    return slopes

In [ ]:
slopes = many_bootstrap_slopes(1000, education, "views", "GPA")
slopes[:5]

In [ ]:
# 95% Confidence Interval
left = percentile(2.5, slopes)
right = percentile(97.5, slopes)
print("Left =", left, ", Right =", right)

In [ ]:
Table().with_column("Bootstrap Slopes", slopes).hist()
plots.plot([left, right], [0,0], color="yellow", lw=8);

Could the true slope be 0?  In other words, could there be no linear relation between the variables?
* Null Hypothesis. The slope of the true line is 0.
* Alternative Hypothesis. The slope of the true line is not 0.

Since the 95% confidence interval for the true slope does not contain 0, we can reject the null hypothesis!